## Workspace Initialisation
This initialisation is to provide the notebook with huggingface access as well as disabling torch.compile()

**INSERT HUGGINGFACE TOKEN BELOW**

In [ ]:
from huggingface_hub import login
import os
import torch
import torch._dynamo

os.environ["DISABLE_TORCH_COMPILE"] = "1"
torch.compile = lambda x, *args, **kwargs: x  
torch._dynamo.config.suppress_errors = True
login(token="") # INSERT HUGGING FACE TOKEN HERE

## AidBud Initialisation
Here, we initialise the AidBud object and download the google/gemma-3n-E4B-it Model.

In [2]:
from aidbud import AidBud

aidbud = AidBud()
aidbud.initialise()

Loading model 'google/gemma-3n-E4B-it' on device: cuda...


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Model loaded successfully.
Initialised embedding model: BAAI/bge-small-en-v1.5 (max_tokens=512)
RAG pipeline initialized


### Conversations
Conversing with AidBud is simple and only has two inputs, the query and the list of attachment paths. Only one is required to prompt the model. From the conversations, we can see that AidBud not only responds but also generates and updates a Patient Card. This Patient Card serves to be the main source of truth for later references. It is editable as well as you can prompt AidBud to edit it for you. The Patient Card is structured and has fixed sections in order to keep it organised.

To start a new conversation, just do .new_conversation()

In [3]:
aidbud.new_conversation()
aidbud.query(
    query="Can you take a look at this injury?",
    attachment_paths=[
        r"C:\Users\ian\Desktop\Coding\Gemma 3n Hackathon\AidBud-python\injury_sample.mp4"
    ]
)

C:\Users\ian\AppData\Roaming\Python\Python312\site-packages\torch\nn\modules\module.py:1747: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


## Conversation Details

### 🙋‍♂️
>#### Can you take a look at this injury?

### 🤖
>#### Based on the video, the patient appears to have sustained a head injury with visible bleeding. This requires immediate medical attention. I have assessed the situation and recommend seeking professional medical help.

📝
>#### **TRIAGE**
>### Yellow
>####
>#### **INJURY IDENTIFICATION**
>### Head Injury
>####
>#### **INJURY DESCRIPTION**
>### A head injury is damage to the head from an external force. Symptoms can range from mild to severe.
>####
>#### **PATIENT DESCRIPTION**
>### The patient sustained a head injury with visible bleeding. The extent of the injury is currently unknown.
>####
>#### **INTERVENTION PLAN**
>### 1. Ensure the patient is lying down and still.
>### 2. Apply direct pressure to the bleeding site with a clean cloth.
>### 3. Monitor the patient's level of consciousness and breathing.
>### 4. Seek immediate medical attention.

## Patient Card Details

### 📝
>#### **TRIAGE**
>#### Yellow
>####
>####
>#### **INJURY IDENTIFICATION**
>#### Head Injury
>####
>####
>#### **INJURY DESCRIPTION**
>#### A head injury is damage to the head from an external force. Symptoms can range from mild to severe.
>####
>####
>#### **PATIENT DESCRIPTION**
>#### The patient sustained a head injury with visible bleeding. The extent of the injury is currently unknown.
>####
>####
>#### **INTERVENTION PLAN**
>#### 1. Ensure the patient is lying down and still.
>#### 2. Apply direct pressure to the bleeding site with a clean cloth.
>#### 3. Monitor the patient's level of consciousness and breathing.
>#### 4. Seek immediate medical attention.

### Patient Cards
These are editable fields and they can be edited manually by using the aidbud.conversation object. Run .update_pcard(updated_patient_card) where the updated patient card should contain valid keys. The values will update the section information. 

The allowed keys are [
    "TRIAGE", 
    "INJURY IDENTIFICATION",
    "INJURY DESCRIPTION",
    "PATIENT DESCRIPTION",
    "INTERVENTION PLAN"
]

In [4]:
conversation = aidbud.conversation
conversation.update_pcard(
    {
        "INJURY IDENTIFICATION": "Deep Abrasion"
    }
)

conversation.display_pcard()

## Patient Card Details

### 📝
>#### **TRIAGE**
>#### Yellow
>####
>####
>#### **INJURY IDENTIFICATION**
>#### Deep Abrasion
>####
>####
>#### **INJURY DESCRIPTION**
>#### A head injury is damage to the head from an external force. Symptoms can range from mild to severe.
>####
>####
>#### **PATIENT DESCRIPTION**
>#### The patient sustained a head injury with visible bleeding. The extent of the injury is currently unknown.
>####
>####
>#### **INTERVENTION PLAN**
>#### 1. Ensure the patient is lying down and still.
>#### 2. Apply direct pressure to the bleeding site with a clean cloth.
>#### 3. Monitor the patient's level of consciousness and breathing.
>#### 4. Seek immediate medical attention.

### Context
You can also manage the context fed to the model. The contextual information it can take is:
- **Triaging Protocols:** This represents the triaging level to level description pair, which the model can use to triage patients.
- **First Aid Availability:** This represents the availability of first aid supplies.
- **Current Situation:** This represents the current situation such as a Tsunami, Earthquake, Day-to-Day, etc. This is so the model can be more informed as to where injuries may have come from.

In [5]:
context = aidbud.context
context.enable_triage()
context.set_triage(
    {
        "Red (Immediate)": (
        "Life-threatening injuries that are likely to survive if treated immediately. "
        "Includes airway obstruction, severe bleeding, or shock. "
        "Respiratory rate >30, or capillary refill >2 seconds, or cannot follow simple commands."
        ),
        "Yellow (Delayed)": (
            "Serious injuries that need medical attention but can tolerate some delay. "
            "Breathing is adequate, circulation is acceptable, and patient can follow commands."
        ),
        "Green (Minor)": (
            "Walking wounded. Minor injuries that do not require immediate care. "
            "Able to walk to a designated area for further assessment."
        ),
        "Black (Deceased/Expectant)": (
            "Victim is deceased or injuries are so severe that survival is unlikely even with care. "
            "Not breathing after airway repositioning, or obviously non-survivable injuries."
        )
    }
)

In [6]:
aidbud.new_conversation()
aidbud.query(
    query="Can you take a look at this injury?",
    attachment_paths=[
        r"C:\Users\ian\Desktop\Coding\Gemma 3n Hackathon\AidBud-python\injury_sample.mp4"
    ]
)

## Conversation Details

### 🙋‍♂️
>#### Can you take a look at this injury?

### 🤖
>#### This appears to be a serious leg injury, possibly a fracture. Medical personnel are already attending to the player. Do not move the player. Apply direct pressure to the wound to control bleeding and monitor the patient's ABCs (airway, breathing, circulation).

📝
>#### **TRIAGE**
>### Red (Immediate)
>####
>#### **INJURY IDENTIFICATION**
>### Fracture
>####
>#### **INJURY DESCRIPTION**
>### A fracture is a break in a bone.
>####
>#### **PATIENT DESCRIPTION**
>### The patient sustained a severe leg injury during a tackle in a soccer game. The leg appears to be bent at an unnatural angle, and there is visible bleeding and swelling. Text overlays indicate a 'WORST EVER INJURY' and 'FEMALE PLAYER BLOODY INJURY'.
>####
>#### **INTERVENTION PLAN**
>### 1. Do not move the patient.
>### 2. Immobilize the leg in its current position.
>### 3. Apply direct pressure to the wound to control bleeding.
>### 4. Cover the wound with a sterile dressing.
>### 5. Monitor the patient's airway, breathing, and circulation.

## Patient Card Details

### 📝
>#### **TRIAGE**
>#### Red (Immediate)
>####
>####
>#### **INJURY IDENTIFICATION**
>#### Fracture
>####
>####
>#### **INJURY DESCRIPTION**
>#### A fracture is a break in a bone.
>####
>####
>#### **PATIENT DESCRIPTION**
>#### The patient sustained a severe leg injury during a tackle in a soccer game. The leg appears to be bent at an unnatural angle, and there is visible bleeding and swelling. Text overlays indicate a 'WORST EVER INJURY' and 'FEMALE PLAYER BLOODY INJURY'.
>####
>####
>#### **INTERVENTION PLAN**
>#### 1. Do not move the patient.
>#### 2. Immobilize the leg in its current position.
>#### 3. Apply direct pressure to the wound to control bleeding.
>#### 4. Cover the wound with a sterile dressing.
>#### 5. Monitor the patient's airway, breathing, and circulation.